In [1]:
from collections import namedtuple
from pathlib import Path

import numpy as np

WORKDIR = Path.cwd().absolute()
INPUTFILE = WORKDIR / "2022-19.txt"

with INPUTFILE.open("r") as file:
    inputs = [line.strip() for line in file.readlines()]

test = [
    "Blueprint 1: Each ore robot costs 4 ore. Each clay robot costs 2 ore. Each obsidian robot costs 3 ore and 14 clay. Each geode robot costs 2 ore and 7 obsidian.",
    "Blueprint 2: Each ore robot costs 2 ore. Each clay robot costs 3 ore. Each obsidian robot costs 3 ore and 8 clay. Each geode robot costs 3 ore and 12 obsidian."
]

inputs = test

for _ in range(min(8, len(inputs))):
    print(inputs[_])

Blueprint 1: Each ore robot costs 4 ore. Each clay robot costs 2 ore. Each obsidian robot costs 3 ore and 14 clay. Each geode robot costs 2 ore and 7 obsidian.
Blueprint 2: Each ore robot costs 2 ore. Each clay robot costs 3 ore. Each obsidian robot costs 3 ore and 8 clay. Each geode robot costs 3 ore and 12 obsidian.


In [2]:
ORE = 0
CLAY = 1
OBSIDIAN = 2
GEODE = 3
COUNT = 4

blueprints = np.zeros((len(inputs), COUNT, COUNT), dtype=np.int8)
for line in inputs:
    line = line.split(" ")
    id = int(line[1][:-1])
    ore_ore_cost = int(line[6])
    clay_ore_cost = int(line[12])
    obisidian_ore_cost = int(line[18])
    obisidian_clay_cost = int(line[21])
    geode_ore_cost = int(line[27])
    geode_obsidian_cost = int(line[30])
    index = id -1
    blueprints[index,ORE,ORE] = ore_ore_cost
    blueprints[index,CLAY,ORE] = clay_ore_cost
    blueprints[index,OBSIDIAN,ORE] = obisidian_ore_cost
    blueprints[index,OBSIDIAN,CLAY] = obisidian_clay_cost
    blueprints[index,GEODE,ORE] = geode_ore_cost
    blueprints[index,GEODE,OBSIDIAN] = geode_obsidian_cost

print(inputs[0])
print(blueprints[0,:,:])
print()
print(inputs[-1])
print(blueprints[-1,:,:])


Blueprint 1: Each ore robot costs 4 ore. Each clay robot costs 2 ore. Each obsidian robot costs 3 ore and 14 clay. Each geode robot costs 2 ore and 7 obsidian.
[[ 4  0  0  0]
 [ 2  0  0  0]
 [ 3 14  0  0]
 [ 2  0  7  0]]

Blueprint 2: Each ore robot costs 2 ore. Each clay robot costs 3 ore. Each obsidian robot costs 3 ore and 8 clay. Each geode robot costs 3 ore and 12 obsidian.
[[ 2  0  0  0]
 [ 3  0  0  0]
 [ 3  8  0  0]
 [ 3  0 12  0]]


In [3]:
def max_geodes(blueprint:np.ndarray, clock:int=0, robots:np.ndarray=np.array([1,0,0,0],dtype=np.int8), resources:np.ndarray=np.zeros(4, dtype=np.int8)) -> int:

    if clock >= 24:
        return resources[GEODE]

    # If we build nothing (action = None), just collect:
    maximum = max_geodes(blueprint, clock+1, robots, resources+robots)

    for robot, cost in enumerate(blueprint):
        if np.all(resources >= cost):
            equipment = np.array(robots)
            equipment[robot] += 1
            geodes = max_geodes(blueprint, clock+1, equipment, resources+robots)
            maximum = max(maximum, geodes)

    return maximum

# print(f"{max_geodes(blueprints[0])=}")
# print(f"{max_geodes(blueprints[-1])=}")


In [6]:
def search(blueprint:np.ndarray, clock:int=0, robots:np.ndarray=np.array([1,0,0,0],dtype=np.int8), resources:np.ndarray=np.zeros(4, dtype=np.int8)) -> int:

    paths = [[0, robots, resources]]
    while len(paths) > 0:
        scenario = paths.pop(0)
        time, bots, stuff = scenario
        if time == 24:
            print(scenario)
            continue

        if time % 5 == 0:
            print(f"Considering {scenario}")

        paths.append([time+1,bots,stuff+bots])
        for robot, cost in enumerate(blueprint):
            if np.all(stuff >= cost):
                equipment = np.array(bots)
                equipment[robot] += 1
                paths.append([time+1,equipment,stuff - cost + bots])

search(blueprints[0])


Considering [0, array([1, 0, 0, 0], dtype=int8), array([0, 0, 0, 0], dtype=int8)]
Considering [5, array([1, 0, 0, 0], dtype=int8), array([5, 0, 0, 0], dtype=int8)]
Considering [5, array([2, 0, 0, 0], dtype=int8), array([1, 0, 0, 0], dtype=int8)]
Considering [5, array([1, 1, 0, 0], dtype=int8), array([3, 0, 0, 0], dtype=int8)]
Considering [5, array([1, 1, 0, 0], dtype=int8), array([3, 1, 0, 0], dtype=int8)]
Considering [5, array([1, 2, 0, 0], dtype=int8), array([1, 1, 0, 0], dtype=int8)]
Considering [5, array([1, 1, 0, 0], dtype=int8), array([3, 2, 0, 0], dtype=int8)]
Considering [5, array([1, 2, 0, 0], dtype=int8), array([1, 2, 0, 0], dtype=int8)]
Considering [10, array([1, 0, 0, 0], dtype=int8), array([10,  0,  0,  0], dtype=int8)]
Considering [10, array([2, 0, 0, 0], dtype=int8), array([6, 0, 0, 0], dtype=int8)]
Considering [10, array([1, 1, 0, 0], dtype=int8), array([8, 0, 0, 0], dtype=int8)]
Considering [10, array([2, 0, 0, 0], dtype=int8), array([7, 0, 0, 0], dtype=int8)]
Consider

: 

: 